In [1]:
import sys
import warnings
warnings.filterwarnings("ignore")
import os
import pickle
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, cohen_kappa_score
import numpy as np
import matplotlib
from matplotlib import pylab
import seaborn as sns
#from IPython.display import display
from tabulate import tabulate
from collections import Counter, defaultdict
import re
import copy
from scipy import stats
from scipy.stats import wilcoxon, ttest_rel, shapiro, entropy
import pandas as pd
from utils import *
sns.set_style("dark")
sns.set(font_scale=1.0)

FILENAMES = ['OBESIDAD', 'OBESIDAD_TIPOS', 'FUMADOR']

MODELS = [
        'svm-n1', 'svm-n1-cregex',
        'rf-n1', 'rf-n1-cregex',
        'bert', 'bert-cregex',
        'zsl', 'zsl-cregex'
         ]

LABELS_CLASSES = {
    'OBESIDAD': ['NEGATIVE', 'POSITIVE'],
    'OBESIDAD_TIPOS': ['MODERATE', 'SEVERE', 'MORBID'],
    'FUMADOR': ['NEGATIVE', 'POSITIVE'],
    }

METRIC = 'F1'

pylab.rcParams["legend.facecolor"] = "white"
pylab.rcParams['figure.facecolor'] = "white"
H = 10
W = 20
CURVES = dict( [ (MODEL, ['_PL_', '_AL_']) for MODEL in MODELS] )

COLORS = {
    'nb-n1_PL_': '#5A5A5A',
    'nb-n1_AL_': '#5A5A5A',
    'nb-n1-cregex_AL_': '#5A5A5A',
    'xgb-n1_PL_': '#1F77B4',
    'xgb-n1_AL_': '#1F77B4',
    'xgb-n1-cregex_AL_': '#1F77B4',
    'rf-n1_PL_': '#9B9B9B',
    'rf-n1_AL_': '#9B9B9B',
    'rf-n1-cregex_AL_': '#9B9B9B',
    'svm-n1_PL_': '#6A0DAD',
    'svm-n1_AL_': '#6A0DAD',
    'svm-n1-cregex_AL_': '#6A0DAD',
    'bert_PL_': '#483D8B',
    'bert_AL_': '#483D8B',
    'bert-cregex_AL_': '#483D8B',
    'zsl_PL_': '#8B008B',
    'zsl_AL_': '#8B008B',
    'zsl-cregex_AL_': '#8B008B',
}
LINES = {
          'nb-n1_PL_': '-',
          'nb-n1_AL_': '--',
          'nb-n1-cregex_AL_': 'dotted',
          'xgb-n1_PL_': '-',
          'xgb-n1_AL_': '--',
          'xgb-n1-cregex_AL_': 'dotted',
          'rf-n1_PL_': '-',
          'rf-n1_AL_': '--',
          'rf-n1-cregex_AL_': 'dotted',
          'svm-n1_PL_': '-',
          'svm-n1_AL_': '--',
          'svm-n1-cregex_AL_': 'dotted',
          'bert_PL_': '-',
          'bert_AL_': '--',
          'bert-cregex_AL_': 'dotted',
          'zsl_PL_': '-',
          'zsl_AL_': '--',
          'zsl-cregex_AL_': 'dotted',
}
LABELS = {
          'nb-n1_PL_': 'NB (PL)',
          'nb-n1_AL_': 'NB (AL)',
          'nb-n1-cregex_AL_': 'NB&RegExes (AL)',
          'xgb-n1_PL_': 'XGB (PL)',
          'xgb-n1_AL_': 'XGB (AL)',
          'xgb-n1-cregex_AL_': 'XGB&RegExes (AL)',
          'rf-n1_PL_': 'RF (PL)',
          'rf-n1_AL_': 'RF (AL)',
          'rf-n1-cregex_AL_': 'RF&RegExes (AL)',
          'svm-n1_PL_': 'SVM (PL)',
          'svm-n1_AL_': 'SVM (AL)',
          'svm-n1-cregex_AL_': 'SVM&RegExes (AL)',
          'bert_PL_': 'BERT (PL)',
          'bert_AL_': 'BERT (AL)',
          'bert-cregex_AL_': 'BERT&RegExes (AL)',
          'zsl_PL_': 'ZSL (PL)',
          'zsl_AL_': 'ZSL (AL)',
          'zsl-cregex_AL_': 'ZSL&RegExes (AL)',
}
TITLES = {
          'OBESIDAD': 'OBESITY STATUS DS',
          'OBESIDAD_TIPOS': 'OBESITY TYPES DS',
          'FUMADOR': 'SMOKING STATUS DS',
}

LW = 2
MS = 5
S = 150

None of PyTorch, TensorFlow >= 2.0, or Flax have been found. Models won't be available and only tokenizers, configuration and file/data utilities can be used.


In [2]:
FOLDS = 5

print('FOLDS:', FOLDS, '\n')

CURVE_AUX = 'RESULTS'

times = defaultdict(list)
results = defaultdict(list)
pred_dst = defaultdict(list)

for FILENAME in FILENAMES:
    #print('-'*30)
    #print(FILENAME)

    for k in range(FOLDS):

        for MODEL in MODELS:
            #print(MODEL)

            with open( os.path.join( os.getcwd(), 'out', 'RESULTS', FILENAME, FILENAME+'_'+MODEL+'_'+CURVE_AUX+'_k'+str(k+1)+'.pkl' ), 'rb') as a:
                results_lc = pickle.load(a)

                p_aux = copy.deepcopy(results_lc[0]).argmax(axis=1)  #prediction values
                t_aux = copy.deepcopy(results_lc[1])                 #time values
                dst_aux = copy.deepcopy(results_lc[2])               #distribution values
                y_train_aux = copy.deepcopy(results_lc[3])           #train labels
                y_test_aux = copy.deepcopy(results_lc[4])            #test labels

                if 'regex' not in MODEL:
                    times[MODEL+'_train_'+FILENAME].append( t_aux[0]/(60*FOLDS) )
                    times[MODEL+'_predict_'+FILENAME].append( t_aux[1]/(60*FOLDS) )
                else:
                    times['RegExs_train_'+FILENAME].append( t_aux[0]/(60*FOLDS) )
                    L = len(y_test_aux)
                    dst = [d[0] for d in dst_aux['predict-'+MODEL] if 'rex' in d]
                    N = len(dst)
                    time_aux = N*(times[MODEL.replace('-cregex', '')+'_predict_'+FILENAME][-1]/L)
                    times['RegExs_predict_'+FILENAME].append(  (t_aux[1]-time_aux)/(60*FOLDS) )

                if len(LABELS_CLASSES[FILENAME])>2:
                    pre = precision_score(y_test_aux, p_aux, average='weighted')
                    rec = recall_score(y_test_aux, p_aux, average='weighted')
                else:
                    pre = precision_score(y_test_aux, p_aux, pos_label=1)
                    rec = recall_score(y_test_aux, p_aux, pos_label=1)
                f1 = (2*pre*rec)/(pre+rec)

                results[MODEL+'_PRE_'+FILENAME].append( pre )
                results[MODEL+'_REC_'+FILENAME].append( rec )
                results[MODEL+'_F1_'+FILENAME].append( f1 )
                
                if 'cregex' in MODEL:
                    pred_dst[MODEL+'_'+FILENAME].append( [ 'rex' if 'rex' in p[0] else 'clf'  for p in dst_aux['predict-'+MODEL] ]  )
                
#print('TIMES')
#for key in times:
#    print(key, np.mean(times[key]), 'std:', np.std(times[key]))

print('\nRESULTS')
for key in results:
    print(key, np.mean(results[key]), 'std:', np.std(results[key]))

FOLDS: 5 


RESULTS
svm-n1_PRE_OBESIDAD 0.9645262972237291 std: 0.014024738346452301
svm-n1_REC_OBESIDAD 0.975718437344599 std: 0.013800352257920204
svm-n1_F1_OBESIDAD 0.9699096425135154 std: 0.004450127351878401
svm-n1-cregex_PRE_OBESIDAD 0.9607948769767427 std: 0.016228547778621347
svm-n1-cregex_REC_OBESIDAD 0.9954946066824519 std: 0.006459951753025524
svm-n1-cregex_F1_OBESIDAD 0.9777190955749578 std: 0.006619517203181106
rf-n1_PRE_OBESIDAD 0.9765738093704075 std: 0.008041911505918018
rf-n1_REC_OBESIDAD 0.9687643044954705 std: 0.012252259127732099
rf-n1_F1_OBESIDAD 0.9725781517409956 std: 0.00593736549628706
rf-n1-cregex_PRE_OBESIDAD 0.9746907576763212 std: 0.00925425385987251
rf-n1-cregex_REC_OBESIDAD 0.9849002316092662 std: 0.00681356145594918
rf-n1-cregex_F1_OBESIDAD 0.9797047894333826 std: 0.0018418360769106587
bert_PRE_OBESIDAD 0.9834859037531561 std: 0.005606481609686412
bert_REC_OBESIDAD 0.9662123444849471 std: 0.006627870761482603
bert_F1_OBESIDAD 0.9747450075666076 std: 0.00

In [14]:
print('\nHYPOTHESIS TESTS')
MODELS_aux = [MODEL for MODEL in MODELS if 'cregex' in MODEL]
METRICS = ['_PRE_','_REC_','_F1_']
alpha = 0.05
count = 0
total = 0
for FILENAME in FILENAMES:
    for METRIC_aux in METRICS:
        for MODEL_aux in MODELS_aux:
            A = np.array(results[MODEL_aux.replace('-cregex', '')+METRIC_aux+FILENAME])
            B = np.array(results[MODEL_aux+METRIC_aux+FILENAME])
            test = 'wilcoxon'
            _, p = wilcoxon(B,A, alternative='greater')
            if p<alpha:
                print(FILENAME, METRIC_aux, MODEL_aux, p, test, A.mean(), B.mean())
                count+=1
            total+=1

print(count/total)


HYPOTHESIS TESTS
OBESIDAD _PRE_ zsl-cregex 0.03125 wilcoxon 0.7851620315339604 0.7931103180900927
OBESIDAD _REC_ svm-n1-cregex 0.03125 wilcoxon 0.975718437344599 0.9954946066824519
OBESIDAD _REC_ bert-cregex 0.03125 wilcoxon 0.9662123444849471 0.9789311604947283
OBESIDAD _F1_ svm-n1-cregex 0.03125 wilcoxon 0.9699096425135154 0.9777190955749578
OBESIDAD _F1_ zsl-cregex 0.03125 wilcoxon 0.8745754133837114 0.8813394602126786
OBESIDAD_TIPOS _PRE_ svm-n1-cregex 0.03125 wilcoxon 0.7935227517992144 0.8585755154714187
OBESIDAD_TIPOS _PRE_ rf-n1-cregex 0.03125 wilcoxon 0.8432728299841624 0.9119363558471012
OBESIDAD_TIPOS _PRE_ bert-cregex 0.03125 wilcoxon 0.8737350854339205 0.9010850231861509
OBESIDAD_TIPOS _PRE_ zsl-cregex 0.03125 wilcoxon 0.7459782643661237 0.8037041212419668
OBESIDAD_TIPOS _REC_ svm-n1-cregex 0.03125 wilcoxon 0.7964725881852954 0.8569364337320138
OBESIDAD_TIPOS _REC_ rf-n1-cregex 0.03125 wilcoxon 0.8371865703357416 0.9075951672636757
OBESIDAD_TIPOS _REC_ bert-cregex 0.03125

In [4]:
sns.set(font_scale=1.5)

FOLDS = 1

print('FOLDS:', FOLDS, '\n')

idx = 0
values = np.arange(0.6, 1, 0.01)
x_y_curves = {'0_'+METRIC.upper()+'(%)>=': values}
results_aulc = defaultdict(list)
#results_base = defaultdict(list)
results_curves = defaultdict(list)
results_features = defaultdict(list)
results_hyps = defaultdict(list)

results_dst = defaultdict(list)
results_thr = defaultdict(list)
results_thr_rex = defaultdict(list)

for FILENAME in FILENAMES:
    #print('-'*30)
    #print(FILENAME)
    idx+=1

    for MODEL in MODELS:
        #print(MODEL)

        for CURVE in CURVES[MODEL]:
            if 'PL' in CURVE and 'regex' in MODEL:# or 'zsl' in MODEL:
                continue
            #print(CURVE)

            CURVE_AUX = CURVE.replace('_', '')
            y = []  #learning curves

            for k in range(FOLDS):
                with open( os.path.join( os.getcwd(), 'out', 'RESULTSLC', CURVE_AUX, FILENAME, FILENAME+'_'+MODEL+'_'+CURVE_AUX+'_k'+str(k+1)+'.pkl' ), 'rb') as a:
                    results_lc = pickle.load(a)
                    y_b = []
                    s_b = []

                    s_aux = copy.deepcopy(results_lc[0])  #entropy values
                    x_aux = copy.deepcopy(results_lc[1])  #x-samples values
                    y_aux = copy.deepcopy(results_lc[2])  #pred on test
                    yl_aux = copy.deepcopy(results_lc[3]) #pred on unlabeled
                    yc_aux = copy.deepcopy(results_lc[4]) #labels on unlabeled
                    d_aux = copy.deepcopy(results_lc[5])  #distribution on test (clf vs rex)
                    h_aux = copy.deepcopy(results_lc[6])  #hyperparameters
                    f_aux = copy.deepcopy(results_lc[7])  #number of features
                    yt_aux = copy.deepcopy(results_lc[8]) #labels on test
                    
                    #print(h_aux)

                    results_hyps[MODEL+'_'+FILENAME].append(h_aux)
                    results_features[MODEL+'_'+FILENAME].append(f_aux)

                    if len(d_aux)>0:
                        dst_cregex_aux = []
                        thr_cregex_aux = []
                        thr_cregex_rex_aux = [] ###
                        for p in range(len(d_aux)):
                            aux_d = []
                            aux_t = []
                            aux_rex_t = [] ###
                            pred_aux = d_aux[p]['predict-'+MODEL]
                            thr_aux = d_aux[p]['thresholds-'+MODEL.replace('-cregex', '')]
                            aux_d.extend( [ keyp[0].replace('-A','').replace('-B','') for keyp in pred_aux ] )
                            f1s = thr_aux[2]
                            thrs = thr_aux[3]
                            if len(LABELS_CLASSES[FILENAME])>2:
                                thrs = thrs[0]
                            idx_max = np.argmax(f1s)
                            dst_cregex_aux.append( Counter(aux_d) )
                            thr_cregex_aux.append( thrs[idx_max] )

                            match_pr = [(keyp[1][-1])[0] for keyp in pred_aux if keyp[0]=='rex' ] ##
                            match_pr.append(np.inf)
                            thr_cregex_rex_aux.extend( match_pr)  ###

                        results_dst[MODEL+'_'+FILENAME].append(dst_cregex_aux)
                        results_thr[MODEL+'_'+FILENAME].append(thr_cregex_aux)
                        results_thr_rex[MODEL+'_'+FILENAME].append(thr_cregex_rex_aux) ###

                    for ypredb in y_aux:
                        if METRIC == 'F1':
                            if len(LABELS_CLASSES[FILENAME])>2:
                                pre =  precision_score(yt_aux, ypredb.argmax(axis=1), average='weighted')
                                rec = recall_score(yt_aux, ypredb.argmax(axis=1), average='weighted')
                            else:
                                pre =  precision_score(yt_aux, ypredb.argmax(axis=1), pos_label=1)
                                rec = recall_score(yt_aux, ypredb.argmax(axis=1), pos_label=1)
                            f1 = (2*pre*rec)/(pre+rec)
                            y_b.append( f1 )
                            
                            '''
                            if 'AL' in CURVE:
                                acc = accuracy_score(yt_aux, ypredb.argmax(axis=1))
                                results_base[MODEL+'_PRE_'+FILENAME] = np.round(pre,2)
                                results_base[MODEL+'_REC_'+FILENAME] = np.round(rec,2)
                                results_base[MODEL+'_F1_'+FILENAME]  = np.round(f1,2)
                                results_base[MODEL+'_ACC_'+FILENAME]  = np.round(acc, 2)
                            '''

                        elif METRIC == 'ACC':
                            acc = accuracy_score(yt_aux, ypredb.argmax(axis=1))
                            y_b.append( acc )

                    y.append(y_b)

            y = np.array(y)
            ye = np.std(y, axis=0)
            y = np.mean(y, axis=0)

            results_curves[MODEL+CURVE+FILENAME] = copy.deepcopy(y)
            results_aulc[MODEL+CURVE+FILENAME] = np.round(AULC(x_aux, y),2)

            #fig1 = pylab.figure(1, figsize=(int(H*1.00),int(W*0.75)), dpi=800)
            fig1 = pylab.figure(1, figsize=(H*1.7,int(W)/3.0),dpi=800)
            #pylab.subplot(len(FILENAMES), 1, idx)
            pylab.subplot(1, len(FILENAMES), idx)
            pylab.title(TITLES[FILENAME], fontweight='bold')
            pylab.plot(x_aux, y, COLORS[MODEL+CURVE], linestyle=LINES[MODEL+CURVE], label=LABELS[MODEL+CURVE], lw=LW, ms=MS)
            #print('Curve', y)
            pylab.fill_between(x_aux, y-ye, y+ye, facecolor=COLORS[MODEL+CURVE],  alpha=0.05)

            pylab.ylim([0.50, 1.00])
            pylab.grid(True)
            pylab.xlabel('Number of training examples'.upper() )
            pylab.ylabel( ('Average '+METRIC).upper() )
            #if idx==2:
            #    pylab.legend( loc='upper center', bbox_to_anchor=(0.50, -1.40), shadow=False, ncol=4 )

            x_y = []
            for val in values:
                xy = '-'
                for i in range(len(x_aux)):
                    if y[i]>=val and xy=='-':
                        xy = x_aux[i]
                        break
                x_y.append(xy)
            x_y_curves[MODEL+CURVE+FILENAME] = x_y
            
            
    '''
    #baseline
    y = [ results['zsl_'+METRIC+'_'+FILENAME][FOLDS-1] ]*len(x_aux)
    pylab.plot(x_aux, y, COLORS['zsl'], linestyle=LINES['zsl'], label=LABELS['zsl'], lw=LW, ms=MS)
    #pylab.axhline(y=y, color=COLORS['zsl'], linestyle=LINES['zsl'], label=LABELS['zsl'], lw=LW)
    '''
    if idx==2:
        #pylab.legend( loc='upper center', bbox_to_anchor=(0.50, -1.40), shadow=False, ncol=5 )
        pylab.legend( loc='upper center', bbox_to_anchor=(0.50, -0.2), shadow=False, ncol=4 )
    


pylab.show()

fig1.savefig( os.path.join(os.getcwd(), 'out', 'Figures', 'lc.pdf'), bbox_inches='tight', format="pdf" )

FOLDS: 1 



In [5]:
print('AULC')
for key in results_aulc:
    #if '_AL_' in key:
    print(key, results_aulc[key])

AULC
svm-n1_PL_OBESIDAD 0.96
svm-n1_AL_OBESIDAD 0.97
svm-n1-cregex_AL_OBESIDAD 0.98
rf-n1_PL_OBESIDAD 0.96
rf-n1_AL_OBESIDAD 0.97
rf-n1-cregex_AL_OBESIDAD 0.97
bert_PL_OBESIDAD 0.96
bert_AL_OBESIDAD 0.96
bert-cregex_AL_OBESIDAD 0.97
zsl_PL_OBESIDAD 0.85
zsl_AL_OBESIDAD 0.85
zsl-cregex_AL_OBESIDAD 0.86
svm-n1_PL_OBESIDAD_TIPOS 0.78
svm-n1_AL_OBESIDAD_TIPOS 0.78
svm-n1-cregex_AL_OBESIDAD_TIPOS 0.86
rf-n1_PL_OBESIDAD_TIPOS 0.8
rf-n1_AL_OBESIDAD_TIPOS 0.81
rf-n1-cregex_AL_OBESIDAD_TIPOS 0.91
bert_PL_OBESIDAD_TIPOS 0.73
bert_AL_OBESIDAD_TIPOS 0.72
bert-cregex_AL_OBESIDAD_TIPOS 0.86
zsl_PL_OBESIDAD_TIPOS 0.73
zsl_AL_OBESIDAD_TIPOS 0.73
zsl-cregex_AL_OBESIDAD_TIPOS 0.76
svm-n1_PL_FUMADOR 0.85
svm-n1_AL_FUMADOR 0.87
svm-n1-cregex_AL_FUMADOR 0.87
rf-n1_PL_FUMADOR 0.86
rf-n1_AL_FUMADOR 0.88
rf-n1-cregex_AL_FUMADOR 0.88
bert_PL_FUMADOR 0.81
bert_AL_FUMADOR 0.81
bert-cregex_AL_FUMADOR 0.83
zsl_PL_FUMADOR 0.78
zsl_AL_FUMADOR 0.78
zsl-cregex_AL_FUMADOR 0.8


In [6]:
print('LC')
for FILENAME in FILENAMES:
    dct = {'0_F1(%)>=':x_y_curves['0_F1(%)>=']}
    for key in x_y_curves:
        if key.endswith(FILENAME):
            dct[key] = x_y_curves[key]
    df = pd.DataFrame.from_dict(dct)
    table_df = tabulate(df, headers = 'keys', tablefmt = 'psql', showindex=False).replace('|', '&')
    table_df = re.sub(r'^\&', ' ', table_df, flags=re.M)
    table_df = re.sub(r'\&$', r'\\\\ ', table_df, flags=re.M)
    print( table_df )
    del dct

LC
+-------------+----------------------+----------------------+-----------------------------+---------------------+---------------------+----------------------------+--------------------+--------------------+---------------------------+-------------------+-------------------+--------------------------+
    0_F1(%)>= & svm-n1_PL_OBESIDAD   & svm-n1_AL_OBESIDAD   & svm-n1-cregex_AL_OBESIDAD   & rf-n1_PL_OBESIDAD   & rf-n1_AL_OBESIDAD   & rf-n1-cregex_AL_OBESIDAD   & bert_PL_OBESIDAD   & bert_AL_OBESIDAD   & bert-cregex_AL_OBESIDAD   & zsl_PL_OBESIDAD   & zsl_AL_OBESIDAD   & zsl-cregex_AL_OBESIDAD   \\ 
 -------------+----------------------+----------------------+-----------------------------+---------------------+---------------------+----------------------------+--------------------+--------------------+---------------------------+-------------------+-------------------+--------------------------\\ 
         0.6  & 64                   & 64                   & 64                       

In [7]:
CURVES_aux = dict( [ (MODEL, ['_AL_']) for MODEL in MODELS] )# if 'zsl' not in MODEL] )
#MODELS_aux = [MODEL for MODEL in MODELS if 'zsl' not in MODEL]

print('FOLDS:', FOLDS, '\n')

idx = 0

for FILENAME in FILENAMES:
    #print('-'*30)
    #print(FILENAME)
    idx+=1

    for MODEL in MODELS: # _aux:
        #print(MODEL)

        for CURVE in CURVES_aux[MODEL]:
            CURVE_AUX = CURVE.replace('_', '')
            y = []  #learning curves
            s = []  #scores-AL

            dst_al = defaultdict(list)
            for k in range(FOLDS):
                with open( os.path.join( os.getcwd(), 'out', 'RESULTSLC', CURVE_AUX, FILENAME, FILENAME+'_'+MODEL+'_'+CURVE_AUX+'_k'+str(k+1)+'.pkl' ), 'rb') as a:
                    results_lc = pickle.load(a)
                    s_b = []

                    s_aux = copy.deepcopy(results_lc[0])  #entropy values
                    x_aux = copy.deepcopy(results_lc[1])  #x-samples values
                    y_aux = copy.deepcopy(results_lc[2])  #pred on test
                    yl_aux = copy.deepcopy(results_lc[3]) #pred on unlabeled
                    yc_aux = copy.deepcopy(results_lc[4]) #labels on unlabeled
                    d_aux = copy.deepcopy(results_lc[5])  #distribution on test (clf vs rex)
                    h_aux = copy.deepcopy(results_lc[6])  #hyperparameters
                    f_aux = copy.deepcopy(results_lc[7])  #number of features
                    yt_aux = copy.deepcopy(results_lc[8]) #labels on test

                    for spredb in s_aux:
                        s_b.append( np.var(spredb[:BATCH]) )
                    s.append(s_b)
                    NPOINTS = len(y_b)

            y = results_curves[MODEL+CURVE+FILENAME]
            s = np.array(s)
            se = np.std(s, axis=0)
            s = np.mean(s, axis=0)

            fig2 = pylab.figure(1, figsize=(H*1.7,int(W)/3.0),dpi=800)
            pylab.subplot(1, len(FILENAMES), idx)
            #fig2 = pylab.figure(2, figsize=(int(H*1.00),int(W*0.75)), dpi=800)
            #pylab.subplot(len(FILENAMES), 1, idx)
            pylab.title(TITLES[FILENAME], fontweight='bold')
            pylab.plot(x_aux[:-1]+1, s, COLORS[MODEL+CURVE], label=LABELS[MODEL+CURVE], linestyle=LINES[MODEL+CURVE],
                       lw=LW,
                       ms=MS)
            pylab.fill_between(x_aux[:-1]+1, s-se, s+se, facecolor=COLORS[MODEL+CURVE],  alpha=0.05)
            m = SC(s)
            pylab.ylim([-0.01, 0.30])
            pylab.grid(True)
            pylab.xlabel( 'iteration number'.upper() )
            pylab.ylabel( 'Average variance'.upper() )
            pylab.xticks(x_aux[:-1]+1, np.arange(1, len(x_aux[:-1])+1))
            if idx==2:
                #pylab.legend( loc='upper center', bbox_to_anchor=(0.50, -1.40), shadow=False, ncol=3 )
                pylab.legend( loc='upper center', bbox_to_anchor=(0.50, -0.2), shadow=False, ncol=4 )
            if m<len(s)-1-2:
                print('SC', FILENAME, MODEL, CURVE,
                      'Deltay', y[m]-y[m+2],
                      'x_%', (100*x_aux[m+2])/x_aux[-1],
                     )

            else:
                diff = len(y)-m-1
                print('SC', FILENAME, MODEL, CURVE, 'Deltay', y[m]-y[m+diff], 'x_%', (100*x_aux[m+diff])/x_aux[-1])


pylab.show()

fig2.savefig( os.path.join(os.getcwd(), 'out', 'Figures', 'var.pdf'), bbox_inches='tight', format="pdf" )


FOLDS: 1 

SC OBESIDAD svm-n1 _AL_ Deltay 0.0028795673625621188 x_% 51.75202156334232
SC OBESIDAD svm-n1-cregex _AL_ Deltay 0.0 x_% 60.37735849056604
SC OBESIDAD rf-n1 _AL_ Deltay -0.0004899514585129383 x_% 51.75202156334232
SC OBESIDAD rf-n1-cregex _AL_ Deltay -0.0057762750070442515 x_% 51.75202156334232
SC OBESIDAD bert _AL_ Deltay 0.0 x_% 51.75202156334232
SC OBESIDAD bert-cregex _AL_ Deltay -0.0030196715016319597 x_% 51.75202156334232
SC OBESIDAD zsl _AL_ Deltay 0.0 x_% 43.1266846361186
SC OBESIDAD zsl-cregex _AL_ Deltay 0.0 x_% 60.37735849056604
SC OBESIDAD_TIPOS svm-n1 _AL_ Deltay 0.012112287124828924 x_% 100.0
SC OBESIDAD_TIPOS svm-n1-cregex _AL_ Deltay -0.02367087072915175 x_% 77.10843373493977
SC OBESIDAD_TIPOS rf-n1 _AL_ Deltay 3.4723969688510437e-05 x_% 88.12392426850258
SC OBESIDAD_TIPOS rf-n1-cregex _AL_ Deltay 0.019845224621298008 x_% 100.0
SC OBESIDAD_TIPOS bert _AL_ Deltay -0.08627568590741563 x_% 88.12392426850258
SC OBESIDAD_TIPOS bert-cregex _AL_ Deltay 0.05348629428

In [8]:
print('HYPERPARAMETERS')
MODELS_aux = [MODEL for MODEL in MODELS if 'zsl' not in MODEL and 'bert' not in MODEL]

aux = defaultdict(list)
for MODEL in MODELS_aux:
    for FILENAME in FILENAMES:
        keys = results_hyps[MODEL+'_'+FILENAME][0]
        for key in keys:
            for k in range(FOLDS):
                aux[MODEL+'_'+key].append( results_hyps[MODEL+'_'+FILENAME][k][key] )

for key in aux:
    print(key, Counter(aux[key]))

HYPERPARAMETERS
svm-n1_random_state Counter({42: 3})
svm-n1_probability Counter({True: 3})
svm-n1_C Counter({1: 3})
svm-n1_kernel Counter({'linear': 3})
svm-n1-cregex_random_state Counter({42: 3})
svm-n1-cregex_probability Counter({True: 3})
svm-n1-cregex_C Counter({1: 3})
svm-n1-cregex_kernel Counter({'linear': 3})
rf-n1_random_state Counter({42: 3})
rf-n1_criterion Counter({'gini': 3})
rf-n1_n_estimators Counter({500: 1, 100: 1, 1000: 1})
rf-n1-cregex_random_state Counter({42: 3})
rf-n1-cregex_criterion Counter({'entropy': 3})
rf-n1-cregex_n_estimators Counter({500: 2, 1000: 1})


In [9]:
sns.set(font_scale=1.5)

MODELS_aux = [MODEL for MODEL in MODELS if 'cregex' in MODEL]# and 'zsl' not in MODEL]

k = 0
idx = 1
fig3 = pylab.figure(3, figsize=(H*1.7,int(W)/3.0),dpi=800)
color = [COLORS[MODEL+'_AL_'] for MODEL in MODELS_aux]
for FILENAME in FILENAMES:
    ax = pylab.subplot(1,3,idx)
    df = defaultdict(list)
    for MODEL in MODELS_aux:
        MODEL_AUX = MODEL.replace('-cregex','').replace('-n1', '').upper()
        dcts = results_dst[MODEL+'_'+FILENAME][k]
        for dct in dcts:
            r =  dct['rex']
            c = dct['clf']
            df[MODEL_AUX].append( (100*r)/(c+r) )
    df = pd.DataFrame.from_dict(df).mean(axis=0)
    df.plot(kind='bar', ax=ax, legend=None, width=0.8, color=color, rot=0)
    pylab.title(TITLES[FILENAME], fontweight='bold')
    pylab.ylim([0,60])
    pylab.ylabel('AVERAGE USE OF RegExes (%)')
    pylab.grid(True)
    idx+=1

fig3.savefig( os.path.join(os.getcwd(), 'out', 'Figures', 'dst.pdf'), bbox_inches='tight', format="pdf" )

In [10]:
sns.set(font_scale=1.5)

MODELS_aux = [MODEL for MODEL in MODELS if 'cregex' in MODEL]# and 'zsl' not in MODEL]

k = 0
idx = 1
fig4 = pylab.figure(4, figsize=(H*1.70,int(W)/3.0),dpi=800)
color = [COLORS[MODEL+'_AL_'] for MODEL in MODELS_aux]
decision = {'OBESIDAD': 1/2, 'OBESIDAD_TIPOS': 1/3, 'FUMADOR': 1/2}
for FILENAME in FILENAMES:
    ax = pylab.subplot(1,3,idx)
    df = defaultdict(list)
    for MODEL in MODELS_aux:
        MODEL_AUX = MODEL.replace('-cregex','').replace('-n1', '').upper()
        thrs = np.copy(results_thr[MODEL+'_'+FILENAME][k])
        thrs = np.mean(thrs)
        df[MODEL_AUX] = [thrs]
    df = pd.DataFrame.from_dict(df).mean(axis=0)
    df.plot(kind='bar', ax=ax, legend=None, width=0.8, color=color, rot=0)
    pylab.title(TITLES[FILENAME], fontweight='bold')
    pylab.ylim([0.0,1.0])
    pylab.ylabel('PROBABILITY THRESHOLD')
    pylab.axhline(y=decision[FILENAME], color='k', linestyle='--')
    pylab.grid(True)
    idx+=1

fig4.savefig( os.path.join(os.getcwd(), 'out', 'Figures', 'thr.pdf'), bbox_inches='tight', format="pdf" )

In [11]:
sns.set(font_scale=1.5)

MODELS_aux = [MODEL for MODEL in MODELS if 'cregex' in MODEL]# and 'zsl' not in MODEL]

k = 0
idx = 1
fig5 = pylab.figure(5, figsize=(H*1.70,int(W)/3.0),dpi=800)
color = [COLORS[MODEL+'_AL_'] for MODEL in MODELS_aux]
decision = {'OBESIDAD': 1/2, 'OBESIDAD_TIPOS': 1/3, 'FUMADOR': 1/2}
for FILENAME in FILENAMES:
    ax = pylab.subplot(1,3,idx)
    df = defaultdict(list)
    for MODEL in MODELS_aux:
        MODEL_AUX = MODEL.replace('-cregex','').replace('-n1', '').upper()
        thrs = copy.deepcopy(results_thr_rex[MODEL+'_'+FILENAME][k])
        while np.inf in thrs:
            thrs.remove(np.inf)
        thrs = np.mean(thrs)
        df[MODEL_AUX] = [thrs]
    df = pd.DataFrame.from_dict(df).mean(axis=0)
    df.plot(kind='bar', ax=ax, legend=None, width=0.8, color=color, rot=0)
    pylab.title(TITLES[FILENAME], fontweight='bold')
    pylab.ylim([0.0,1.0])
    pylab.ylabel('PROBABILITY THRESHOLD')
    pylab.axhline(y=decision[FILENAME], color='k', linestyle='--')
    pylab.grid(True)
    idx+=1

fig5.savefig( os.path.join(os.getcwd(), 'out', 'Figures', 'thr_rex.pdf'), bbox_inches='tight', format="pdf" )